In [43]:
! pip install langchain-groq

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 109.6/109.6 kB 7.6 MB/s eta 0:00:00


In [28]:
pip install requests tqdm Pillow matplotlib fitz langchain langchain-chroma langchain-ollama huggingface_hub


  Using cached tokenizers-0.20.3-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (6.7 kB)
Using cached tokenizers-0.20.3-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.0 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.21.0
    Uninstalling tokenizers-0.21.0:
      Successfully uninstalled tokenizers-0.21.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
transformers 4.47.1 requires tokenizers<0.22,>=0.21, but you have tokenizers 0.20.3 which is incompatible.


In [29]:
import os
import io
import re
import uuid
import base64
import shutil
import requests
from tqdm import tqdm
from PIL import Image
import matplotlib.pyplot as plt
from IPython.display import HTML, display
import fitz
from langchain_core.documents import Document
from langchain_text_splitters import CharacterTextSplitter
from langchain.storage import InMemoryStore
from langchain_chroma import Chroma
from langchain.chains.llm import LLMChain, PromptTemplate
from langchain_core.messages import HumanMessage, SystemMessage
from langchain_core.prompts.chat import (ChatPromptTemplate, HumanMessagePromptTemplate, SystemMessagePromptTemplate)
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnableLambda, RunnablePassthrough
from langchain.retrievers.multi_vector import MultiVectorRetriever
from langchain_ollama import OllamaLLM
from langchain.embeddings import HuggingFaceEmbeddings

In [30]:
embeddings = HuggingFaceEmbeddings(model_name='BAAI/bge-large-en')

In [31]:
import fitz

def extract_text_and_tables(pdf_path):
    doc = fitz.open(pdf_path)
    texts = []
    tables = []

    for page in doc:
        page_text = page.get_text("text").split("\n")
        texts.extend(page_text)
        tables += page.get_text("dict")["blocks"]

    return texts, tables

pdf_path = "/content/DeepSeek_R1.pdf"
texts, tables = extract_text_and_tables(pdf_path)

print("Text from PDF:")
print(texts)

print("\nTables from PDF:")
for table in tables:
    print(table)


Text from PDF:
['DeepSeek-R1: Incentivizing Reasoning Capability in LLMs via', 'Reinforcement Learning', 'DeepSeek-AI', 'research@deepseek.com', 'Abstract', 'We introduce our first-generation reasoning models, DeepSeek-R1-Zero and DeepSeek-R1.', 'DeepSeek-R1-Zero, a model trained via large-scale reinforcement learning (RL) without super-', 'vised fine-tuning (SFT) as a preliminary step, demonstrates remarkable reasoning capabilities.', 'Through RL, DeepSeek-R1-Zero naturally emerges with numerous powerful and intriguing', 'reasoning behaviors. However, it encounters challenges such as poor readability, and language', 'mixing. To address these issues and further enhance reasoning performance, we introduce', 'DeepSeek-R1, which incorporates multi-stage training and cold-start data before RL. DeepSeek-', 'R1 achieves performance comparable to OpenAI-o1-1217 on reasoning tasks. To support the', 'research community, we open-source DeepSeek-R1-Zero, DeepSeek-R1, and six dense models', '(1.5B

In [35]:
from transformers import AutoProcessor, AutoModelForImageTextToText

processor = AutoProcessor.from_pretrained("Salesforce/blip-image-captioning-base")
model = AutoModelForImageTextToText.from_pretrained("Salesforce/blip-image-captioning-base")

In [33]:
!pip install colab-xterm
%load_ext colabxterm

The colabxterm extension is already loaded. To reload it, use:
  %reload_ext colabxterm


In [ ]:
ollama serve &

In [ ]:
curl -fsSL https://ollama.com/install.sh | sh

In [36]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [37]:
import os
os.environ['OLLAMA_HOST'] = '127.0.0.1:11434'

In [38]:
from langchain_community.llms import Ollama

llm = Ollama(model="llava")

response = llm.invoke("How many years in a century.")
print(response)

 A century consists of 100 years, so it is equal to 100 years. 


In [39]:
text_splitter = CharacterTextSplitter.from_tiktoken_encoder(
    chunk_size = 1000, chunk_overlap = 0
)
joined_texts = " ".join(texts)
texts_token = text_splitter.split_text(joined_texts)

print("No of Textual Chunks:", len(texts))
print("No of Table Elements:", len(tables))
print("No of Text Chunks after Tokenization:", len(texts_token))

No of Textual Chunks: 1403
No of Table Elements: 304
No of Text Chunks after Tokenization: 1


In [41]:
print("No of Textual Chunks:", len(texts))


No of Textual Chunks: 1403


In [40]:
def generate_text_summaries(texts, tables, summarize_texts=False):
    """
    Summarize text elements
    texts: List of str
    tables: List of str
    summarize_texts: Bool to summarize texts
    """

    prompt_text = """You are an assistant tasked with summarizing tables for retrieval. \
    Give a concise summary of the table that is well optimized for retrieval. Make sure to capture all the details. \
    Input: {element} """
    prompt = ChatPromptTemplate.from_template(prompt_text)

    summarize_chain = {"element": lambda x: x} | prompt | llm | StrOutputParser()

    text_summaries = []
    table_summaries = []

    if texts and summarize_texts:
        text_summaries = summarize_chain.batch(texts, {"max_concurrency": 3})
    elif texts:
        text_summaries = texts

    if tables:
        table_summaries = summarize_chain.batch(tables, {"max_concurrency": 3})
        return text_summaries, table_summaries
text_summaries, table_summaries = generate_text_summaries(
    texts_token, tables, summarize_texts=False
)

In [42]:
print("No of Text Summaries:", len(text_summaries))
print("No of Table Summaries:", len(table_summaries))

No of Text Summaries: 1
No of Table Summaries: 304


In [47]:
from langchain_groq import ChatGroq
vlm_client = ChatGroq(
    temperature=0,
    groq_api_key = "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",
    model_name="llama-3.3-70b-versatile"
)

In [ ]:

def encode_image(image_path):
    """Getting the base64 string"""
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode("utf-8")

def image_summarize(img_base64, prompt):
    """Make image summary"""
    chat_response = vlm_client.chat.completions.create(
        model="llava-hf/llava-1.5-7b-hf",
        max_tokens=1024,
        messages=[{
            "role": "user",
            "content": [
                {"type": "text", "text": prompt},
                {
                    "type": "image_url",
                    "image_url": {
                        "url": f"data:image/jpeg;base64,{img_base64}",
                    },
                },
            ],
        }],
        stream=False
    )
    return chat_response.choices[0].message.content.strip()

In [54]:


def generate_img_summaries(path):
    """
    Generate summaries and base64 encoded strings for images
    path: Path to list of .jpg files extracted by Unstructured
    """
    img_base64_list = []
    image_summaries = []
    prompt = """You are an assistant tasked with summarizing images for optimal retrieval. \
    These summaries will be embedded and used to retrieve the raw image.
    Write a clear and concise summary that captures all the important information, including any statistics or key points present in the image."""
    for img_file in tqdm(sorted(os.listdir(path))):
        if img_file.endswith(".jpg"):
            img_path = os.path.join(path, img_file)
            base64_image = encode_image(img_path)
            img_base64_list.append(base64_image)
            generated_summary = image_summarize(base64_image, prompt)
            print(generated_summary)
            image_summaries.append(generated_summary)
    return img_base64_list, image_summaries


img_base64_list, image_summaries = generate_img_summaries(folder_path)
assert len(img_base64_list) == len(image_summaries)

0it [00:00, ?it/s]


In [51]:
folder_path = "./data/"

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [53]:
import os

if not os.path.exists(folder_path):
        os.makedirs(folder_path)

In [55]:
def create_multi_vector_retriever(vectorstore, text_summaries, texts, table_summaries, tables, image_summaries, images):

    store = InMemoryStore()
    id_key = "doc_id"
    retriever = MultiVectorRetriever(
        vectorstore=vectorstore,
        docstore=store,
        id_key=id_key,
    )
    def add_documents(retriever, doc_summaries, doc_contents):
        doc_ids = [str(uuid.uuid4()) for _ in doc_contents]
        summary_docs = [
            Document(page_content=s, metadata={id_key: doc_ids[i]})
            for i, s in enumerate(doc_summaries)
        ]
        retriever.vectorstore.add_documents(summary_docs)
        retriever.docstore.mset(list(zip(doc_ids, doc_contents)))
    if text_summaries:
        add_documents(retriever, text_summaries, texts)
    if table_summaries:
        add_documents(retriever, table_summaries, tables)
    if image_summaries:
        add_documents(retriever, image_summaries, images)
    return retriever

vectorstore = Chroma(
    collection_name="mm_rag_vectorstore", embedding_function=embeddings, persist_directory="./chroma_db"
)


retriever_multi_vector_img = create_multi_vector_retriever(
    vectorstore,
    text_summaries,
    texts,
    table_summaries,
    tables,
    image_summaries,
    img_base64_list,
)

In [56]:
def plt_img_base64(img_base64):

    image_html = f'<img src="data:image/jpeg;base64,{img_base64}" />'
    display(HTML(image_html))

def looks_like_base64(sb):
    """Check if the string looks like base64"""
    return re.match("^[A-Za-z0-9+/]+[=]{0,2}$", sb) is not None

def is_image_data(b64data):
    """
    Check if the base64 data is an image by looking at the start of the data
    """
    image_signatures = {
        b"\xff\xd8\xff": "jpg",
        b"\x89\x50\x4e\x47\x0d\x0a\x1a\x0a": "png",
        b"\x47\x49\x46\x38": "gif",
        b"\x52\x49\x46\x46": "webp",
    }
    try:
        header = base64.b64decode(b64data)[:8]
        for sig, format in image_signatures.items():
            if header.startswith(sig):
                return True
        return False
    except Exception:
        return False

def resize_base64_image(base64_string, size=(64, 64)):

    img_data = base64.b64decode(base64_string)
    img = Image.open(io.BytesIO(img_data))
    resized_img = img.resize(size, Image.LANCZOS)
    buffered = io.BytesIO()
    resized_img.save(buffered, format=img.format)
    return base64.b64encode(buffered.getvalue()).decode("utf-8")

def split_image_text_types(docs):

    b64_images = []
    texts = []
    for doc in docs:
        if isinstance(doc, Document):
            doc = doc.page_content
        if looks_like_base64(doc) and is_image_data(doc):
            doc = resize_base64_image(doc, size=(64, 64))
            b64_images.append(doc)
        else:
            texts.append(doc)
    return {"images": b64_images, "texts": texts}

def img_prompt_func(data_dict):
    """
    Join the context into a single string
    """
    formatted_texts = "\n".join(data_dict["context"]["texts"])
    messages = []
    text_message = {
        "type": "text",
        "text": (
            "You are an AI assistant with expertise in finance and business metrics.\n"
            "You will be given information that may include text, tables, and charts related to business performance and industry trends.\n"
            "Your task is to analyze this information and provide a clear, concise answer to the user's question.\n"
            "Focus on the most relevant data points and insights that directly address the user's query.\n"
            f"User's question: {data_dict['question']}\n\n"
            "Information provided:\n"
            f"{formatted_texts}"
        ),
    }
    messages.append(text_message)
    if data_dict["context"]["images"]:
        for image in data_dict["context"]["images"]:
            image_message = {
                "type": "image_url",
                "image_url": {"url": f"data:image/jpeg;base64,{image}"},
            }
            messages.append(image_message)
    return [HumanMessage(content=messages)]

def multi_modal_rag_context_chain(retriever):
    """Multi-modal RAG context chain"""
    chain = (
        {
            "context": retriever | RunnableLambda(split_image_text_types),
            "question": RunnablePassthrough(),
        }
        | RunnableLambda(img_prompt_func)
    )
    return chain


chain_multimodal_context = multi_modal_rag_context_chain(retriever_multi_vector_img)

In [59]:
query = "Benchmark performance of DeepSeek-R1."
docs = retriever_multi_vector_img.invoke(query)

In [60]:
plt_img_base64(docs[0])
